In [1]:
import sys
import os
analysis_dir_path = '../'
sys.path.append(analysis_dir_path)

import models
import pandas as pd
import warnings
import example as ep
warnings.filterwarnings('ignore')

In [2]:
# filters = 32
# kernels = 5
# units = 128

In [3]:
# CNN = f'CNN_{filters}_filters_{kernels}_kernels_predictions'
# CNNA = f'CNN_Attention_{filters}_filters_{kernels}_kernels_predictions'
# RNN = f'RNN_{units}_units_predictions'
# LSTM = f'LSTM_{units}_layers_predictions'

# name_maps = {
#     CNN: "CNN",
#     CNNA: "CNN With Attention",
#     RNN: "RNN",
#     LSTM: "LSTM"
# }

In [4]:
model_check = ep.model_select(f'../cobalt_shift_new_20/test/results_test.csv')
print(model_check)

Highest F1: {'Precision (1)': 0.8225806451612904, 'Recall (1)': 0.6538461538461539, 'F1 (1)': 0.7285714285714286} at model - CNN_256_filters_3_kernels_predictions
Highest Recall: {'Precision (1)': 0.8225806451612904, 'Recall (1)': 0.6538461538461539, 'F1 (1)': 0.7285714285714286} at model - CNN_256_filters_3_kernels_predictions
Highest Precision: {'Precision (1)': 0.9375, 'Recall (1)': 0.1923076923076923, 'F1 (1)': 0.3191489361702128} at model - CNN_Attention_128_filters_5_kernels_predictions
Lowest F1: {'Precision (1)': 0.25, 'Recall (1)': 0.0128205128205128, 'F1 (1)': 0.024390243902439} at model - LSTM_32_layers_predictions
{'Highest F1': {'model': 'CNN_256_filters_3_kernels_predictions', 'metrics': {'Precision (1)': 0.8225806451612904, 'Recall (1)': 0.6538461538461539, 'F1 (1)': 0.7285714285714286}}, 'Highest Recall': {'model': 'CNN_256_filters_3_kernels_predictions', 'metrics': {'Precision (1)': 0.8225806451612904, 'Recall (1)': 0.6538461538461539, 'F1 (1)': 0.7285714285714286}}, '

In [5]:
# %%capture

# COMMODITY = 'nickel_no_val_20'
# MODEL = CNNA
# RULE_NUM = 10
# confidence_levels = [0.4, 0.45, 0.5, 0.55, 0.6, 0.7, 0.8, 0.9, 0.95]

def exclude_zero(series):
    temp = series.copy()
    temp = temp[temp != 0]
    temp = temp[temp != 1]
    return temp

# A function for providing useful labels for the results
def label(results, row):
    labels = []
    max_base_model_precision = exclude_zero(results["Precision (Base Model)"]).max()
    max_base_model_recall = exclude_zero(results["Recall (Base Model)"]).max()
    max_base_model_f1 = exclude_zero(results["F1 (Base Model)"]).max()
    min_base_model_f1 = exclude_zero(results["F1 (Base Model)"]).min()

    if max_base_model_precision == row["Precision (Base Model)"]: labels.append("Best Precision")
    if max_base_model_recall == row["Recall (Base Model)"]: labels.append("Best Recall")
    if max_base_model_f1 == row["F1 (Base Model)"]: labels.append("Best F1")
    if min_base_model_f1 == row["F1 (Base Model)"]: labels.append("Worst F1")
    return ', '.join(labels)

def evaluate_df(df, properties={}):
    # Base model metrics are now passed directly in properties
    precision = properties.get('Base Precision', 0)
    recall = properties.get('Base Recall', 0)
    f1 = properties.get('Base F1', 0)
    prior = df["corr"].sum() / len(df) if len(df) else 0

    df.to_numpy().dump('data/test.npy')
    df = ep.run_edcr()

    new_precision = df.iloc[50]["pre"] if len(df) > 50 else 0
    new_recall = df.iloc[50]["recall"] if len(df) > 50 else 0
    new_f1 = df.iloc[50]["F1"] if len(df) > 50 else 0

    percent_precision = ((new_precision - precision) / precision) if precision != 0 else 0
    percent_recall = ((new_recall - recall) / recall) if recall != 0 else 0
    percent_f1 = ((new_f1 - f1) / f1) if f1 != 0 else 0

    return {
        **properties,
        "Precision (Base Model)": precision,
        "Recall (Base Model)": recall,
        "F1 (Base Model)": f1,
        "Prior": prior,
        "Precision (EDCR)": new_precision,
        "Recall (EDCR)": new_recall,
        "F1 (EDCR)": new_f1,
        "Precision Improvement": new_precision - precision,
        "Recall Improvement": new_recall - recall,
        "F1 Improvement": new_f1 - f1,
        "Precision Improvement (%)": percent_precision,
        "Recall Improvement (%)": percent_recall,
        "F1 Improvement (%)": percent_f1
    }


## Top N F1 Method

In [6]:
for COMMODITY in [
    # 'cobalt_20'
    # 'cobalt_20', 'cobalt_no_val_20', 'cobalt_shift_20', 'cobalt_streaming_20', 'cobalt_20',
    # 'copper_20', 'copper_no_val_20', 'copper_shift_20', 'copper_streaming_20', 'copper_20',
    # 'magnesium_20', 'magnesium_no_val_20', 'magnesium_shift_20', 'magnesium_streaming_20', 'magnesium_20',
    # 'nickel_20', 'nickel_no_val_20', 'nickel_shift_20', 'nickel_streaming_20', 'nickel_20'
    # 'cobalt_20', 'copper_20', 'magnesium_20', 'nickel_20', 
    'cobalt_shift_new_20', 'copper_shift_new_20', 'magnesium_shift_new_20', 'nickel_shift_new_20',
]:
    results = []
    model_metrics = ep.model_select(f'../{COMMODITY}/test/results_test.csv')
    print(f'({COMMODITY}): {model_metrics}')
    
    for model_key, model_info in model_metrics.items():
        model_name = model_info['model']
        base_metrics = model_info['metrics']
        
        for ALGO in ['correction', 'detection_correction']:
            for RULE_NUM in [50]:
                for ablate_models in [None,'LSTM', 'CNNA', 'CNN', 'RNN']:
                # for ablate_models in ['LSTM', 'CNNA', 'CNN', 'RNN']:
                    df_path = f'../{COMMODITY}/test/predictions/test/{model_name}.csv'
                    df = models.npy_to_top_n_f1_bowpy(df_path, f'../{COMMODITY}/test/predictions/test_{ALGO}', RULE_NUM, ablate_models)
                    
                    # Pass the model's base metrics along with other properties to evaluate_df
                    properties = {
                        "Model": model_name,
                        "Exclude": ablate_models,
                        "Algorithm": ALGO,
                        "Rule Num": RULE_NUM,
                        "Base Precision": base_metrics['Precision (1)'],
                        "Base Recall": base_metrics['Recall (1)'],
                        "Base F1": base_metrics['F1 (1)'],
                    }
                    result = evaluate_df(df, properties)
                    results.append(result)

    results_df = pd.DataFrame(results)
    results_df['Label'] = results_df.apply(lambda x: label(results_df, x), axis=1)
    results_df.to_excel(f'out/top_f1/{COMMODITY}_results.xlsx', index=False)

Highest F1: {'Precision (1)': 0.8225806451612904, 'Recall (1)': 0.6538461538461539, 'F1 (1)': 0.7285714285714286} at model - CNN_256_filters_3_kernels_predictions
Highest Recall: {'Precision (1)': 0.8225806451612904, 'Recall (1)': 0.6538461538461539, 'F1 (1)': 0.7285714285714286} at model - CNN_256_filters_3_kernels_predictions
Highest Precision: {'Precision (1)': 0.9375, 'Recall (1)': 0.1923076923076923, 'F1 (1)': 0.3191489361702128} at model - CNN_Attention_128_filters_5_kernels_predictions
Lowest F1: {'Precision (1)': 0.25, 'Recall (1)': 0.0128205128205128, 'F1 (1)': 0.024390243902439} at model - LSTM_32_layers_predictions
(cobalt_shift_new_20): {'Highest F1': {'model': 'CNN_256_filters_3_kernels_predictions', 'metrics': {'Precision (1)': 0.8225806451612904, 'Recall (1)': 0.6538461538461539, 'F1 (1)': 0.7285714285714286}}, 'Highest Recall': {'model': 'CNN_256_filters_3_kernels_predictions', 'metrics': {'Precision (1)': 0.8225806451612904, 'Recall (1)': 0.6538461538461539, 'F1 (1)': 

## Threshold method

In [7]:
# for COMMODITY in [
#     # 'cobalt_shift_20', 
#     # 'copper_shift_20', 'magnesium_shift_20', 'nickel_shift_20',
#     'cobalt_shift_new_20', 
#     'copper_shift_new_20', 'magnesium_shift_new_20', 'nickel_shift_new_20',
# ]:
#     results = []
#     model_metrics = ep.model_select(f'../{COMMODITY}/test/results_test.csv')
#     print(f'({COMMODITY}): {model_metrics}')

#     for model_key, model_info in model_metrics.items():
#         model_name = model_info['model']
#         base_metrics = model_info['metrics']

#         for ALGO in ['correction', 'detection_correction']:
#             # for THRESHOLD in [0.1, 0.15, 0.2, 0.25, 0.3, 0.35, 0.4, 0.45, 0.5]:
#             for THRESHOLD in [0.5]:
#                 df_path = f'../{COMMODITY}/test/predictions/test/{model_name}.csv'
#                 df = models.npy_to_threshold_f1_bowpy(df_path, f'../{COMMODITY}/test/predictions/test_{ALGO}', THRESHOLD, exclude_models=[])

#                 # Pass the model's base metrics along with other properties to evaluate_df
#                 properties = {
#                     "Model": model_name,
#                     "Algorithm": ALGO,
#                     "Threshold": THRESHOLD,
#                     "Base Precision": base_metrics['Precision (1)'],
#                     "Base Recall": base_metrics['Recall (1)'],
#                     "Base F1": base_metrics['F1 (1)'],
#                 }
#                 result = evaluate_df(df, properties)
#                 results.append(result)

#     results_df = pd.DataFrame(results)
#     results_df['Label'] = results_df.apply(lambda x: label(results_df, x), axis=1)
#     results_df.to_excel(f'out/threshold/{COMMODITY}_test_results.xlsx', index=False)
